#### Read in Moral Foundation Dictionary

In [2]:
#File Path to Moral Foundations Dictionary
dic_file_path = 'moral foundations dictionary.dic'

moral_foundations_dict = {} # dictionary to map moral foundation to it's numeric key
word_to_moral_foundation = {} #dictionary to of word to moral foundation

line_counter = 0 #first 12 lines of dic contain the moral foundations and their numeric keys
with open(dic_file_path, 'r', encoding='utf-8') as file:
    for line in file:
        if line.strip() and not line.startswith('%'):
            parts = line.strip().split()
            moral_found =  parts[0]
            moral_found_code = parts[1:] #
            # Add to dictionary (note: you might need to adjust parsing logic)
            if line_counter < 12: #first 12 lines contain the moral foundations and their keys
                moral_foundations_dict[moral_found] = moral_found_code[0]
            else: #rest of lines contain words
                cats = [moral_foundations_dict[cat] for cat in moral_found_code]
                word_to_moral_foundation[moral_found] = cats
        line_counter+=1


In [3]:
moral_foundations_dict

{'01': 'HarmVirtue',
 '02': 'HarmVice',
 '03': 'FairnessVirtue',
 '04': 'FairnessVice',
 '05': 'IngroupVirtue',
 '06': 'IngroupVice',
 '07': 'AuthorityVirtue',
 '08': 'AuthorityVice',
 '09': 'PurityVirtue',
 '10': 'PurityVice',
 '11': 'MoralityGeneral'}

In [4]:
word_to_moral_foundation
len(word_to_moral_foundation)

324

#### Expand Moral Foundation Dictionary with Word2Vec

Use HuggingFace Pre-trained model on tweets.

In [5]:
import gensim.downloader as api

model = api.load("glove-twitter-25")

In [6]:
word_to_moral_foundation_expanded = word_to_moral_foundation.copy()
expanded_dictionary = {}

similarity_threshold = 0.85

for word, categories in word_to_moral_foundation_expanded.items():
    if word in model.key_to_index:
        similar_words = model.most_similar(positive=[word], topn=100)

        for similar_word, similarity_score in similar_words:
            if similarity_score >= similarity_threshold:
                expanded_dictionary[similar_word] = categories

word_to_moral_foundation_expanded.update(expanded_dictionary)

In [7]:
len(word_to_moral_foundation_expanded)

3131

In [8]:
word_to_moral_foundation_expanded

{'safe*': ['HarmVirtue'],
 'peace*': ['HarmVirtue'],
 'compassion*': ['HarmVirtue'],
 'empath*': ['HarmVirtue'],
 'sympath*': ['HarmVirtue'],
 'care': ['HarmVirtue'],
 'caring': ['HarmVirtue'],
 'protect*': ['HarmVirtue'],
 'shield': ['HarmVirtue'],
 'shelter': ['HarmVirtue'],
 'amity': ['HarmVirtue'],
 'secur*': ['HarmVirtue'],
 'benefit*': ['HarmVirtue'],
 'defen*': ['HarmVirtue'],
 'guard*': ['HarmVirtue'],
 'preserve': ['HarmVirtue', 'AuthorityVirtue', 'PurityVirtue'],
 'harm*': ['HarmVice'],
 'suffer*': ['HarmVice'],
 'war': ['HarmVice'],
 'wars': ['HarmVice'],
 'warl*': ['HarmVice'],
 'warring': ['HarmVice'],
 'fight*': ['HarmVice'],
 'violen*': ['HarmVice'],
 'hurt*': ['HarmVice'],
 'kill': ['HarmVice'],
 'kills': ['HarmVice'],
 'killer*': ['HarmVice'],
 'killed': ['HarmVice'],
 'killing': ['HarmVice'],
 'endanger*': ['HarmVice'],
 'cruel*': ['HarmVice'],
 'brutal*': ['HarmVice'],
 'abuse*': ['HarmVice'],
 'damag*': ['HarmVice'],
 'ruin*': ['HarmVice', 'PurityVice'],
 'ravage': 

#### Read in the Reddit Data

In [9]:
import pickle
!ls

with open('/Users/kathryn/Projects/Advanced ML/project/climate-conversations/project/data_collection/project_data/climateCommentsDf.pickle', 'rb') as f:
    comments_df = pickle.load(f)

with open('/Users/kathryn/Projects/Advanced ML/project/climate-conversations/project/data_collection/project_data/climateSubmissionsDf.pickle', 'rb') as f:
    submissions_df = pickle.load(f)

comments.csv                     moral_found_dict_generator.py
gensim-data                      reddit_analysis.ipynb
moral foundations dictionary.dic


/var/folders/r5/kpzsq4n95zscm639kmnjc7zh0000gn/T/ipykernel_821/1334400979.py:5: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  comments_df = pickle.load(f)


In [10]:
comments_df.head()
subset_comments_df = comments_df.iloc[0:1000]

subset_comments_df.head()

id  subreddit             body                author  score  gilded  \
0  inlvurb   politics        [removed]             [deleted]      1       0   
1  inlw0wi  worldnews  Needed a laugh!  serious-activity-228      3       0   
2  inlx8g7   politics        [deleted]             [deleted]      1       0   
3  inlxwat  worldnews           Asked!           dieyoufool3      3       0   
4  inlyusw  worldnews        [deleted]             [deleted]      1       0   

   created_utc parent_id link_id  retrieved_on  controversiality  is_submitter  
0   1662654718    x8y56x  x8y56x    1665086767                 0         False  
1   1662654781   inlvhve  x8yhv5    1665086761                 0         False  
2   1662655233   inkxrse  x8y56x    1665086718                 0         False  
3   1662655481   inlszmb  x94ag0    1665086696                 0          True  
4   1662655839   inlyqzt  x8yhv5    1665086662                 0         False

In [11]:
subset_comments_df.to_csv("comments.csv")

In [13]:
import sys
sys.path.append('/Users/kathryn/Projects/Advanced ML/project/climate-conversations')

from project.utils.classes.tokenizer import Tokenizer
tokenizer = Tokenizer(filepath='comments.csv', filename='tokenized_comments.csv')
tokenizer.process(cols_to_tokenize=[('body', 'tokenized_body')])

In [14]:
tokenizer.tokenized_df

Unnamed: 0       id  subreddit  \
0             0  inlvurb   politics   
1             1  inlw0wi  worldnews   
2             2  inlx8g7   politics   
3             3  inlxwat  worldnews   
4             4  inlyusw  worldnews   
..          ...      ...        ...   
995         995  iqkeu9y  worldnews   
996         996  iqkeubx  worldnews   
997         997  iqkeuck  worldnews   
998         998  iqkeucs   politics   
999         999  iqkeuep    science   

                                                  body                author  \
0                                            [removed]             [deleted]   
1                                      Needed a laugh!  serious-activity-228   
2                                            [deleted]             [deleted]   
3                                               Asked!           dieyoufool3   
4                                            [deleted]             [deleted]   
..                                                 ...                   ...   
995  isn't russia the country that did everything t...              leifnoto   
996  I mean makes sense. Throw every officer and ge...              dani_vic   
997           That's right! You're not our buddy, guy!          panda-normal   
998  &gt;&gt;smart people acting like dopes\n\nNo, ...   alltheyeatislettuce   
999  But that would be and say it with me kids obje...  obvious_biscotti_832   

     score  gilded  created_utc parent_id link_id  retrieved_on  \
0        1       0   1662654718    x8y56x  x8y56x    1665086767   
1        3       0   1662654781   inlvhve  x8yhv5    1665086761   
2        1       0   1662655233   inkxrse  x8y56x    1665086718   
3        3       0   1662655481   inlszmb  x94ag0    1665086696   
4        1       0   1662655839   inlyqzt  x8yhv5    1665086662   
..     ...     ...          ...       ...     ...           ...   
995     37       0   1664582984    xsenkm  xsenkm    1664960531   
996      2       0   1664582984   iqkehgq  xrrpuq    1664960531   
997      3       0   1664582984    xsb3jw  xsb3jw    1664960531   
998      1       0   1664582985    xs0i5d  xs0i5d    1664960531   
999      0       0   1664582985    xsanb1  xsanb1    1664960531   

     controversiality  is_submitter  \
0                   0         False   
1                   0         False   
2                   0         False   
3                   0          True   
4                   0         False   
..                ...           ...   
995                 0         False   
996                 0         False   
997                 0         False   
998                 0         False   
999                 0         False   

                                  tokenized_body_sents  \
0                                          [[removed]]   
1                                    [needed a laugh!]   
2                                          [[deleted]]   
3                                             [asked!]   
4                                          [[deleted]]   
..                                                 ...   
995  [isn't russia the country that did everything ...   
996  [i mean makes sense., throw every officer and ...   
997        [that's right!, you're not our buddy, guy!]   
998  [&gt;&gt;smart people acting like dopes\n\nno,...   
999  [but that would be and say it with me kids obj...   

                                  tokenized_body_words  \
0                                            [removed]   
1                                      [needed, laugh]   
2                                            [deleted]   
3                                              [asked]   
4                                            [deleted]   
..                                                 ...   
995  [russia, country, escalate, war, like, nato, a...   
996  [mean, makes, sense, throw, officer, general, ...   
997                                [right, buddy, guy]   
998  [gt;&gt;smart, peop

In [15]:
def assign_moral_foundations(comment, extended_dict):
    foundations = {}
    for word in comment:
        for key, foundation_values in extended_dict.items():
            # Ensure foundation_values is a list for consistency
            if not isinstance(foundation_values, list):
                foundation_values = [foundation_values]
            
            for value in foundation_values:
                if key.endswith('*') and word.startswith(key[:-1]):
                    # Increment the foundation's count
                    foundations[value] = foundations.get(value, 0) + 1
                elif word == key:
                    # Increment the foundation's count
                    foundations[value] = foundations.get(value, 0) + 1
    return foundations

# Assuming tokenizer.tokenized_df['tokenized_body_words_norm'] contains lists of words for each comment
tokenizer.tokenized_df['moral_foundations'] = tokenizer.tokenized_df['tokenized_body_words_norm'].apply(
    lambda x: assign_moral_foundations(x, word_to_moral_foundation_expanded)
)

In [16]:
tokenizer.tokenized_df['moral_foundations']

0                                                     {}
1                                 {'MoralityGeneral': 1}
2                                                     {}
3                                                     {}
4                                                     {}
                             ...                        
995    {'PurityVirtue': 1, 'HarmVice': 1, 'MoralityGe...
996    {'MoralityGeneral': 7, 'HarmVirtue': 1, 'Purit...
997                               {'MoralityGeneral': 2}
998    {'IngroupVirtue': 1, 'HarmVirtue': 1, 'Moralit...
999            {'MoralityGeneral': 2, 'PurityVirtue': 1}
Name: moral_foundations, Length: 1000, dtype: object

In [18]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline

import moralstrength
from moralstrength.lexicon_use import form_text_vector
from moralstrength.estimators import estimate

from gsitk.preprocess import pprocess_twitter, simple, Preprocessor

In [47]:
from moralstrength.moralstrength import estimate_morals, models, string_moral_values

texts = tokenizer.tokenized_df['tokenized_body_sents']

for text in texts:
    text = text
    print(text)
    #result = estimate_morals(text, process=True) # set to false if text is alredy pre-processed
    result = string_moral_values(text[0], model='unigram+freq')
    print(result)


['[removed]']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['needed a laugh!']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['[deleted]']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['asked!']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['[deleted]']


/Users/kathryn/Library/Caches/pypoetry/virtualenvs/climate-conversations-9uZwomFh-py3.11/lib/python3.11/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator LogisticRegression from version 1.1.3 when using version 1.4.1.post1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/kathryn/Library/Caches/pypoetry/virtualenvs/climate-conversations-9uZwomFh-py3.11/lib/python3.11/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator CountVectorizer from version 1.1.3 when using version 1.4.1.post1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/kathryn/Library/Caches/pypoetry/vi

{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['[deleted]']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['soviet planes do not crash.']
{'care': 0.45710977866231184, 'fairness': 0.40053123501041876, 'loyalty': 0.04458018795655627, 'authority': 0.3684710379078417, 'purity': 0.12571725952988658, 'non-moral': 0.06315545172225111}
['[deleted]']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['i thought he was in london']
{'care': 0.07231742266811518, 'fairness': 0.04748130387790942, 'loyalty': 0.04344969593221794, 'authority': 0.028501746693417

/Users/kathryn/Library/Caches/pypoetry/virtualenvs/climate-conversations-9uZwomFh-py3.11/lib/python3.11/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator LogisticRegression from version 1.1.3 when using version 1.4.1.post1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/kathryn/Library/Caches/pypoetry/virtualenvs/climate-conversations-9uZwomFh-py3.11/lib/python3.11/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator CountVectorizer from version 1.1.3 when using version 1.4.1.post1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/kathryn/Library/Caches/pypoetry/vi

{'care': 0.039491987582384834, 'fairness': 0.08097898136980541, 'loyalty': 0.02633971662167872, 'authority': 0.0376478479160803, 'purity': 0.030027832274419235, 'non-moral': 0.2974316912190617}
['rest in peace']
{'care': 0.9987631831170409, 'fairness': 0.989736873458993, 'loyalty': 0.3965980075531473, 'authority': 0.31848029259987815, 'purity': 0.9513181050739656, 'non-moral': 0.759080064433417}
['[removed]']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['[deleted]']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['[deleted]']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, '

...

/Users/kathryn/Library/Caches/pypoetry/virtualenvs/climate-conversations-9uZwomFh-py3.11/lib/python3.11/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator CountVectorizer from version 1.1.3 when using version 1.4.1.post1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/kathryn/Library/Caches/pypoetry/virtualenvs/climate-conversations-9uZwomFh-py3.11/lib/python3.11/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator LogisticRegression from version 1.1.3 when using version 1.4.1.post1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/kathryn/Library/Caches/pypoetry/vi

{'care': 0.07153502488610557, 'fairness': 0.09937674523246459, 'loyalty': 0.07985666748528318, 'authority': 0.0556116315199113, 'purity': 0.05581458244350143, 'non-moral': 0.5178039396055809}
['[removed]']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['[deleted]']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
["isn't russia the country that did everything to escalate every part of this war?", "like nato allies didn't help ukraine until after the invasion.", 'strange.']
{'care': 0.9957803806252631, 'fairness': 0.9999214994297139, 'loyalty': 0.9609258179871866, 'authority': 0.9871932477388113, 'purity': 0.9997833595973277, 'non-moral': 0.00036032060393028015}
['i mean makes sense.', 'throw 

/Users/kathryn/Library/Caches/pypoetry/virtualenvs/climate-conversations-9uZwomFh-py3.11/lib/python3.11/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator LogisticRegression from version 1.1.3 when using version 1.4.1.post1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/kathryn/Library/Caches/pypoetry/virtualenvs/climate-conversations-9uZwomFh-py3.11/lib/python3.11/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator CountVectorizer from version 1.1.3 when using version 1.4.1.post1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/kathryn/Library/Caches/pypoetry/vi

{'care': 0.973364554491427, 'fairness': 0.988835021050118, 'loyalty': 0.9717453278338611, 'authority': 0.9999652041726514, 'purity': 0.9981097419245588, 'non-moral': 0.13444850027606717}
['&gt;&gt;smart people acting like dopes\n\nno, a significant chunk of those folks are all day, every day, actually fucking idiots.']
{'care': 0.9505158208350167, 'fairness': 0.9828458831305831, 'loyalty': 0.9890554885979359, 'authority': 0.7720035961643854, 'purity': 0.9969471340712414, 'non-moral': 0.015354180827449439}
['but that would be and say it with me kids objectification.', 'women objectify who knew?']
{'care': 0.9995005285843259, 'fairness': 0.9996364246407816, 'loyalty': 0.994877726514292, 'authority': 0.9689762734572857, 'purity': 0.9985165300687397, 'non-moral': 0.0001784982159505403}


/Users/kathryn/Library/Caches/pypoetry/virtualenvs/climate-conversations-9uZwomFh-py3.11/lib/python3.11/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator LogisticRegression from version 1.1.3 when using version 1.4.1.post1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/kathryn/Library/Caches/pypoetry/virtualenvs/climate-conversations-9uZwomFh-py3.11/lib/python3.11/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator CountVectorizer from version 1.1.3 when using version 1.4.1.post1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/kathryn/Library/Caches/pypoetry/vi